In [44]:
from langchain_community.agent_toolkits import create_sql_agent
from langchain_openai import ChatOpenAI
from langchain_groq import ChatGroq
from langchain_core.prompts import ChatPromptTemplate
from langchain_core.pydantic_v1 import BaseModel, Field
import pandas as pd
from pydantic import BaseModel, Field

from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain_community.vectorstores import Chroma
from langchain.embeddings import HuggingFaceEmbeddings
from langchain_core.runnables import RunnablePassthrough
from langchain_core.output_parsers import StrOutputParser


gpt = ChatOpenAI(model="gpt-3.5-turbo", temperature=0)
#agent_gpt_executor = create_sql_agent(gpt, db=db, agent_type="tool-calling", verbose=True)

## make database
from langchain_community.utilities import SQLDatabase
from sqlalchemy import create_engine

from langchain.prompts import ChatPromptTemplate
from langchain.schema import SystemMessage
from langchain_core.prompts import MessagesPlaceholder
#agent_groq_executor = create_sql_agent(llm, db=db, agent_type="tool-calling", verbose=True)

from OpenAITools.FetchTools import fetch_clinical_trials, fetch_clinical_trials_jp
from OpenAITools.CrinicalTrialTools import QuestionModifierEnglish, TumorNameExtractor, SimpleClinicalTrialAgent,GraderAgent,LLMTranslator,generate_ex_question_English

from OpenAITools.JRCTTools import get_matched_df
from sentence_transformers import SentenceTransformer
from sentence_transformers import util
groq = ChatGroq(model_name="llama3-70b-8192", temperature=0)
#agent_groq_executor = create_sql_agent(groq, db=db, agent_type="tool-calling", verbose=True)

import ast
import torch
age = "65"
sex ="男性"
tumor_type ="glioma"
#tumor_type = "gastric cancer"
GeneMutation ="HER2"
Meseable = "有り"
Biopsiable = "有り"
NCTID = 'NCT06441994'

#Define extractor
Translator = LLMTranslator(groq)
TumorName = Translator.translate(tumor_type)
selectionModel =  SentenceTransformer('pritamdeka/S-PubMedBert-MS-MARCO')
ex_question = generate_ex_question_English(age, sex, TumorName, GeneMutation, Meseable, Biopsiable)

/Users/satoc/miniforge3/envs/gradio/lib/python3.12/site-packages/transformers/tokenization_utils_base.py:1617: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be deprecated in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


In [45]:
basedf = pd.read_csv("../ClinicalTrialCSV/JRCT20241215CancerPost.csv", index_col=0)

In [46]:
df = get_matched_df(basedf=basedf, query=TumorName, model=selectionModel, threshold=0.925)
df['AgentJudgment'] = None
df['AgentGrade'] = None

/var/folders/yw/qz00x75d7kb98f7vm8dkhkvw0000gn/T/ipykernel_49357/2492212482.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['AgentJudgment'] = None
/var/folders/yw/qz00x75d7kb98f7vm8dkhkvw0000gn/T/ipykernel_49357/2492212482.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['AgentGrade'] = None


In [47]:
df

JRCT ID       NCT No JapicCTI No  \
82   jRCT2051240121  NCT06413706         NaN   
175  jRCT2031240090          NaN         NaN   
263  jRCT2041230136          NaN         NaN   
361  jRCT2051230069          NaN         NaN   
414  jRCT2031230007          NaN         NaN   
636  jRCT2031210299          NaN         NaN   
712  jRCT2031200153          NaN         NaN   

                                                 Title      TargetJ  \
82   放射線療法後の悪性神経膠腫の小児および若年成人を対象に、アベマシクリブ＋テモゾロミドとテモゾ...       悪性神経膠腫   
175  再発悪性神経膠腫に対する治療用放射性薬剤64Cu-ATSMの有効性を検証するランダム化比較医...       悪性神経膠腫   
263                   再発膠芽腫に対するTUG1を標的とした核酸医薬医師主導第I相試験        再発膠芽腫   
361  神経膠腫患者に対するロムスチン療法とプロカルバジン、ロムスチン、ビンクリスチン併⽤療法の安全...         神経膠腫   
414  BRAF融合遺伝子陽性の進行・再発の低悪性度神経膠腫または膵癌に対するビニメチニブの第Ⅱ相医...  低悪性度神経膠腫、膵癌   
636                     再発悪性神経膠腫患者を対象としたDSP-0390の第1相試験     再発悪性神経膠腫   
712                     Cellm-001による初発膠芽腫治療効果無作為比較対照試験          膠芽腫   

          Target                        TargetEnglish  \
82        悪性神経膠腫                    High-Grade Glioma   
175       悪性神経膠腫                     Malignant glioma   
263        再発膠芽腫               recurrent glioblastoma   
361         神経膠腫                               Glioma   
414  低悪性度神経膠腫、膵癌  Low-grade glioma, pancreatic cancer   
636     再発悪性神経膠腫          Recurrent High-Grade Glioma   
712          膠芽腫                         glioblastoma   

                                              研究・治験の目的 試験等のフェーズ  試験の種類  ...  \
82   放射線療法後の悪性神経膠腫を有する小児および若年成人を対象に、アベマシクリブとテモゾロミドの...        2    NaN  ...   
175  再発・難治性悪性神経膠腫を対象として、64Cu-diacetyl-bis(N4-methyl...        3    NaN  ...   
263  再発膠芽腫患者を対象としてTUG1ASOを投与した場合の投与時の安全性を検討し、至適投与量を...        1    NaN  ...   
361  神経膠腫患者におけるロムスチン療法とプロカルバジン、ロムスチン、ビンクリスチン併用療法の安全...        1    NaN  ...   
414  BRAF融合遺伝子または遺伝子再構成陽性の切除不能または再発の低悪性度神経膠腫(コホート A...        2    NaN  ...   
636  再発悪性神経膠腫患者を対象にDSP-0390を経口投与したときの安全性、薬物動態、薬力学及び...        1    NaN  ...   
712  脳腫瘍のうち、初発悪性膠芽腫に対する自家脳腫瘍免疫賦活剤であるCellm-001について、術...        3    NaN  ...   

        Age Minimum      Age Maximum Gender Discontinuation Criteria  \
82         No limit    21age old not    NaN                      NaN   
175  18age old over  75age old under   Both                      NaN   
263  18age old over  75age old under   Both                      NaN   
361  18age old over         No limit   Both                      NaN   
414  12age old over         No limit   Both                      NaN   
636  18age old over         No limit   Both                      NaN   
712  18age old over  75age old under   Both                      NaN   

                                               Keyword  \
82                                                 NaN   
175  glioblastoma, grade3/4 astrocytoma, grade3 oli...   
263                                                NaN   
361                                                NaN   
414  BRAF fusion gene, BRAF rearrangement, low-grad...   
636                                                NaN   
712                                                NaN   

                                       Intervention(s)  \
82   Drug: Abemaciclib Administered orally Other Na...   
175  Group A: BPC Therapy Depending on the patient'...   
263  Dosing frequency: 1 time /week Dose Levels Lev...   
361  <cohort1> Lomustine 130 mg/m2 orally every 6 w...   
414  Binimetinib is administered 45 mg orally, twic...   
636  Patients will receive DSP-0390 orally once dai...   
712  Inject the investigational drug (Cellm-001 or ...   

                                    TargetWord  \
82                       ['High-Grade Glioma']   
175                       ['Malignant Glioma']   
263              ['Recurrent', 'Glioblastoma']   
361                                 ['Glioma']   
414  ['Low-Grade Glioma', 'Pancreatic Cancer']   
636         ['Recurrent', 'High-Grade Glioma']   
712                           ['Glioblastoma']   

                                             TargetVec Agent

In [48]:

df['AgentJudgment'] = None
df['AgentGrade'] = None

#Define agents
#modifier = QuestionModifierEnglish(groq)
CriteriaCheckAgent = SimpleClinicalTrialAgent(groq)
grader_agent = GraderAgent(groq)

/var/folders/yw/qz00x75d7kb98f7vm8dkhkvw0000gn/T/ipykernel_49357/1375088122.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['AgentJudgment'] = None
/var/folders/yw/qz00x75d7kb98f7vm8dkhkvw0000gn/T/ipykernel_49357/1375088122.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['AgentGrade'] = None


In [49]:
df.iloc[0,:]['Inclusion Criteria']
df.iloc[0,:]['Exclusion Criteria']

'Patients who meets any of the following criteria cannot participate in this clinical trial. -Diffuse Intrinsic Pontine Glioma (DIPG) or diffuse midline glioma located in the ? -Recurrent or refractory HGG including any recurrence/progression during/after radiotherapy. -Secondary HGG, defined as a previously treated low-grade glioma that now meets high- grade criteria, or that resulted from a previously treated malignancy. -Have known pathogenic somatic mutations appropriate for an anaplastic lymphoma kinase (ALK), B-rapidly accelerated fibrosarcoma (BRAF), or neurotrophic tyrosine receptor kinase (NTRK ) inhibitor, in regions where these therapies are available and deemed appropriate by the investigator. -Prior HGG treatment (including bevacizumab), except for surgery and radiotherapy (with or without concomitant temozolomide) -Current enrollment in another trial deemed. -Treatment with an investigational product within the last 30 days or 5 half-lives (whichever is longer). -Prior ma

In [50]:
def GetJRCTCriteria(dataframe, idx):
    InC = dataframe.iloc[idx,:]['Inclusion Criteria']
    ExC = dataframe.iloc[idx,:]['Exclusion Criteria']
    return "Inclusion Criteria :" + InC + "\n" + "Exclusion Criteria :" + ExC

In [51]:
TargetCriteria = GetJRCTCriteria(df,0)

In [52]:
AgentJudgment = CriteriaCheckAgent.evaluate_eligibility(TargetCriteria, ex_question)
print(AgentJudgment)

The patient is eligible for this clinical trial based on the provided information, as there are no exclusion criteria that would prevent him from participating.


In [53]:
AgentGrade = grader_agent.evaluate_eligibility(AgentJudgment)

In [54]:
AgentGrade

'yes'

In [55]:
ex_question = generate_ex_question_English(age, sex, TumorName, GeneMutation, Meseable, Biopsiable)

In [56]:
for i in range(len(df)):
    TargetCriteria = GetJRCTCriteria(df, i)
    AgentJudgment = CriteriaCheckAgent.evaluate_eligibility(TargetCriteria, ex_question)
    print(AgentJudgment)
    AgentGrade = grader_agent.evaluate_eligibility(AgentJudgment)
    print(AgentGrade)
    
    # df.locを使って値を代入（行・列名で指定）
    df.loc[df.index[i], 'AgentJudgment'] = AgentJudgment
    df.loc[df.index[i], 'AgentGrade'] = AgentGrade


The patient is eligible for this clinical trial based on the provided information, as there are no exclusion criteria that would prevent him from participating.
yes
The patient is eligible for this clinical trial based on the provided information, as the patient meets the inclusion criteria (age, measurable and biopsiable tumor, and no exclusion criteria mentioned).
yes
The patient is not eligible for this clinical trial because the patient's age (65) exceeds the upper limit of 75 years old specified in inclusion criterion (7).
no
Based on the provided information, the patient is eligible for this clinical trial. The patient meets the inclusion criteria for Cohort 1, as they have a glioma (WHO Grade 2-4) diagnosed by pathological diagnosis of resection or biopsy, have a history of chemotherapy or radiation therapy, and have measurable lesions based on the RANO criteria. The patient's age of 65 meets the age requirement, and there is no mention of any exclusion criteria that would preve

for i in range(len(df)):
    TargetCriteria = GetJRCTCriteria(df,i)
    AgentJudgment = CriteriaCheckAgent.evaluate_eligibility(TargetCriteria, ex_question)
    print(AgentJudgment)
    AgentGrade = grader_agent.evaluate_eligibility(AgentJudgment)
    print(AgentGrade)
    df.iloc[i,:]['AgentJudgment'] = AgentJudgment
    df.iloc[i,:]['AgentJudgment'] = AgentGrade


In [58]:
df

JRCT ID       NCT No JapicCTI No  \
82   jRCT2051240121  NCT06413706         NaN   
175  jRCT2031240090          NaN         NaN   
263  jRCT2041230136          NaN         NaN   
361  jRCT2051230069          NaN         NaN   
414  jRCT2031230007          NaN         NaN   
636  jRCT2031210299          NaN         NaN   
712  jRCT2031200153          NaN         NaN   

                                                 Title      TargetJ  \
82   放射線療法後の悪性神経膠腫の小児および若年成人を対象に、アベマシクリブ＋テモゾロミドとテモゾ...       悪性神経膠腫   
175  再発悪性神経膠腫に対する治療用放射性薬剤64Cu-ATSMの有効性を検証するランダム化比較医...       悪性神経膠腫   
263                   再発膠芽腫に対するTUG1を標的とした核酸医薬医師主導第I相試験        再発膠芽腫   
361  神経膠腫患者に対するロムスチン療法とプロカルバジン、ロムスチン、ビンクリスチン併⽤療法の安全...         神経膠腫   
414  BRAF融合遺伝子陽性の進行・再発の低悪性度神経膠腫または膵癌に対するビニメチニブの第Ⅱ相医...  低悪性度神経膠腫、膵癌   
636                     再発悪性神経膠腫患者を対象としたDSP-0390の第1相試験     再発悪性神経膠腫   
712                     Cellm-001による初発膠芽腫治療効果無作為比較対照試験          膠芽腫   

          Target                        TargetEnglish  \
82        悪性神経膠腫                    High-Grade Glioma   
175       悪性神経膠腫                     Malignant glioma   
263        再発膠芽腫               recurrent glioblastoma   
361         神経膠腫                               Glioma   
414  低悪性度神経膠腫、膵癌  Low-grade glioma, pancreatic cancer   
636     再発悪性神経膠腫          Recurrent High-Grade Glioma   
712          膠芽腫                         glioblastoma   

                                              研究・治験の目的 試験等のフェーズ  試験の種類  ...  \
82   放射線療法後の悪性神経膠腫を有する小児および若年成人を対象に、アベマシクリブとテモゾロミドの...        2    NaN  ...   
175  再発・難治性悪性神経膠腫を対象として、64Cu-diacetyl-bis(N4-methyl...        3    NaN  ...   
263  再発膠芽腫患者を対象としてTUG1ASOを投与した場合の投与時の安全性を検討し、至適投与量を...        1    NaN  ...   
361  神経膠腫患者におけるロムスチン療法とプロカルバジン、ロムスチン、ビンクリスチン併用療法の安全...        1    NaN  ...   
414  BRAF融合遺伝子または遺伝子再構成陽性の切除不能または再発の低悪性度神経膠腫(コホート A...        2    NaN  ...   
636  再発悪性神経膠腫患者を対象にDSP-0390を経口投与したときの安全性、薬物動態、薬力学及び...        1    NaN  ...   
712  脳腫瘍のうち、初発悪性膠芽腫に対する自家脳腫瘍免疫賦活剤であるCellm-001について、術...        3    NaN  ...   

        Age Minimum      Age Maximum Gender Discontinuation Criteria  \
82         No limit    21age old not    NaN                      NaN   
175  18age old over  75age old under   Both                      NaN   
263  18age old over  75age old under   Both                      NaN   
361  18age old over         No limit   Both                      NaN   
414  12age old over         No limit   Both                      NaN   
636  18age old over         No limit   Both                      NaN   
712  18age old over  75age old under   Both                      NaN   

                                               Keyword  \
82                                                 NaN   
175  glioblastoma, grade3/4 astrocytoma, grade3 oli...   
263                                                NaN   
361                                                NaN   
414  BRAF fusion gene, BRAF rearrangement, low-grad...   
636                                                NaN   
712                                                NaN   

                                       Intervention(s)  \
82   Drug: Abemaciclib Administered orally Other Na...   
175  Group A: BPC Therapy Depending on the patient'...   
263  Dosing frequency: 1 time /week Dose Levels Lev...   
361  <cohort1> Lomustine 130 mg/m2 orally every 6 w...   
414  Binimetinib is administered 45 mg orally, twic...   
636  Patients will receive DSP-0390 orally once dai...   
712  Inject the investigational drug (Cellm-001 or ...   

                                    TargetWord  \
82                       ['High-Grade Glioma']   
175                       ['Malignant Glioma']   
263              ['Recurrent', 'Glioblastoma']   
361                                 ['Glioma']   
414  ['Low-Grade Glioma', 'Pancreatic Cancer']   
636         ['Recurrent', 'High-Grade Glioma']   
712                           ['Glioblastoma']   

                                             TargetVec  \
82

In [59]:
df.columns

Index(['JRCT ID', 'NCT No', 'JapicCTI No', 'Title', 'TargetJ', 'Target',
       'TargetEnglish', '研究・治験の目的', '試験等のフェーズ', '試験の種類', '無作為化', '盲検化', '対照',
       '割付け', '研究目的', '主たる選択基準', '主たる除外基準', '年齢下限', '年齢上限', '性別', '中止基準',
       '対象疾患キーワード', '介入の内容', 'URL', 'Phase', 'Study Type', 'allocation',
       'masking', 'control', 'assignment', 'purpose', 'Inclusion Criteria',
       'Exclusion Criteria', 'Age Minimum', 'Age Maximum', 'Gender',
       'Discontinuation Criteria', 'Keyword', 'Intervention(s)', 'TargetWord',
       'TargetVec', 'AgentJudgment', 'AgentGrade'],
      dtype='object')

In [62]:
 # 列を指定した順に並び替え
columns_order = ['JRCT ID', 'Title', '研究・治験の目的','AgentJudgment', 'AgentGrade','主たる選択基準', '主たる除外基準','Inclusion Criteria','Exclusion Criteria','NCT No', 'JapicCTI No']
df = df[columns_order]

In [63]:
df

JRCT ID                                              Title  \
82   jRCT2051240121  放射線療法後の悪性神経膠腫の小児および若年成人を対象に、アベマシクリブ＋テモゾロミドとテモゾ...   
175  jRCT2031240090  再発悪性神経膠腫に対する治療用放射性薬剤64Cu-ATSMの有効性を検証するランダム化比較医...   
263  jRCT2041230136                   再発膠芽腫に対するTUG1を標的とした核酸医薬医師主導第I相試験   
361  jRCT2051230069  神経膠腫患者に対するロムスチン療法とプロカルバジン、ロムスチン、ビンクリスチン併⽤療法の安全...   
414  jRCT2031230007  BRAF融合遺伝子陽性の進行・再発の低悪性度神経膠腫または膵癌に対するビニメチニブの第Ⅱ相医...   
636  jRCT2031210299                     再発悪性神経膠腫患者を対象としたDSP-0390の第1相試験   
712  jRCT2031200153                     Cellm-001による初発膠芽腫治療効果無作為比較対照試験   

                                              研究・治験の目的  \
82   放射線療法後の悪性神経膠腫を有する小児および若年成人を対象に、アベマシクリブとテモゾロミドの...   
175  再発・難治性悪性神経膠腫を対象として、64Cu-diacetyl-bis(N4-methyl...   
263  再発膠芽腫患者を対象としてTUG1ASOを投与した場合の投与時の安全性を検討し、至適投与量を...   
361  神経膠腫患者におけるロムスチン療法とプロカルバジン、ロムスチン、ビンクリスチン併用療法の安全...   
414  BRAF融合遺伝子または遺伝子再構成陽性の切除不能または再発の低悪性度神経膠腫(コホート A...   
636  再発悪性神経膠腫患者を対象にDSP-0390を経口投与したときの安全性、薬物動態、薬力学及び...   
712  脳腫瘍のうち、初発悪性膠芽腫に対する自家脳腫瘍免疫賦活剤であるCellm-001について、術...   

                                         AgentJudgment AgentGrade  \
82   The patient is eligible for this clinical tria...        yes   
175  The patient is eligible for this clinical tria...        yes   
263  The patient is not eligible for this clinical ...         no   
361  Based on the provided information, the patient...        yes   
414  The patient is not eligible for this clinical ...         no   
636  Based on the provided criteria, the 65-year-ol...    unclear   
712  The patient is eligible for this clinical tria...    unclear   

                                               主たる選択基準  \
82   以下の基準をすべて満たす必要がある ‐生検によって、以下に示す2016 年WHO分類グレード...   
175  1) 登録前直近の病理診断により組織学的にWHO2021に基づく悪性神経膠腫(膠芽腫または、...   
263  (1)手術摘出検体又は生検検体の永久標本にて、組織学的に膠芽腫と診断されている患者 (2)標...   
361  <コホート1>以下のすべての項目を満たすものとする。 1)摘出術又は生検の病理診断にて、神経...   
414  コホートA、コホートB共通の適格規準 1) 保険診療下で行われているNGSを用いたがん遺伝子...   
636  1. 3ヵ月以上の生存が見込める患者 2. 前治療(化学療法、手術又は放射線療法)による副作...   
712  (1)年齢は満18歳以上、75歳以下である。 (2)テント上の膠芽腫(WHO Grade I...   

                                               主たる除外基準  \
82   以下の基準のいずれかに該当する場合、本治験へ参加できない。 ‐びまん性橋膠腫(diffuse...   
175  1) 登録前2年以内の他の悪性腫瘍の既往または合併を有する。ただし局所治療により治癒と判断さ...   
263  (1)脳外転移のある患者 (2)著明な頭蓋内圧亢進症状のある患者 (3)初発時又は再発・増悪...   
361  <コホート1、コホート2共通> 1) 活動性の重複がんを有する(同時性重複がん/多発がん及び...   
414  1) 活動性の重複がんを有する(ただし、次の1~3は除外しない:1完全切除された以下のがん:...   
636  1. Day 1前の3ヵ月以内にベバシズマブ又はその他の血管内皮増殖因子(VEGF)阻害薬に...   
712  (1)登録前14日以内の副腎皮質ステロイド剤(10mg/日超のプレドニゾロン、あるいは相当量...   

                                    Inclusion Criteria  \
82   Subjects required to meet all the folloiwng cr...   
175  1) Histologically diagnosed as high grade glio...   
263  (1) Patients with a histological diagnosis of ...   
361  <Cohort 1> All of the following items shall be...   
414  Inclusion criteria for both cohort A and B 1) ...   
636  1. Estimated life expectancy >= 3 months 2. Re...   
712  (1) 18 years old or older and 75 years old or ...   

                                    Exclusion Criteria       NCT No  \
82   Patients who meets any of the following criter...  NCT06413706   
175  1) Have a history or merger of other malignanc...          NaN   
263  (1) Patients with extracerebral metastases. (2...          NaN   
361  <Common to Cohort 1 and Cohort 2> 1) Active mu...          NaN   
414  1) Active double primary cancer (but not (1)-(...          NaN   
636  1. Prior therapy with bevacizumab or other ant...          NaN   
712  (1) Systemic administration of corticosteroids...          NaN   

    JapicCTI No  
82          NaN  
175         NaN  
263         NaN  
361         NaN  
414         NaN  
636         NaN  
712         NaN

In [5]:
 # 列を指定した順に並び替え
columns_order = ['NCTID', 'AgentGrade', 'Title', 'AgentJudgment', 'Japanes Locations', 
                     'Primary Completion Date', 'Cancer', 'Summary', 'Eligibility Criteria']
df = df[columns_order]        

In [6]:
df

NCTID AgentGrade                                              Title  \
0  NCT05580562         no  ONC201 in H3 K27M-mutant Diffuse Glioma Follow...   
1  NCT06413706        yes  A Study Comparing Abemaciclib Plus Temozolomid...   
2  NCT05503264         no  A Study To Evaluate The Efficacy, Safety, Phar...   
3  NCT06159478         no  Binimetinib in Patients With BRAF Fusion-posit...   

                                       AgentJudgment  \
0  The patient is not eligible for this clinical ...   
1  The patient is eligible for this clinical tria...   
2  The patient is not eligible for this clinical ...   
3  The patient is not eligible for this clinical ...   

                                   Japanes Locations Primary Completion Date  \
0          Chuo City, Fukuoka, Kyoto, Osaka, Sapporo                 2026-08   
1                               Nagoya, Osaka, Tokyo                 2027-07   
2  Aichi, Chiba, Fukuoka, Gifu, Hokkaido, Hyogo, ...              2026-06-23   
3  Fukuoka, Kashiwa, Kyoto City, Sapporo, Sendai, ku              2027-02-28   

                                              Cancer  \
0                                    H3 K27M, Glioma   
1                                             Glioma   
2  NMDAR Autoimmune Encephalitis, LGI1 Autoimmune...   
3                Low-grade Glioma, Pancreatic Cancer   

                                             Summary  \
0  This is a randomized, double-blind, placebo-co...   
1  The purpose of this study is to measure the be...   
2  The purpose of this study is to assess the eff...   
3  This study is an open-label, parallel, 2-cohor...   

                                Eligibility Criteria  
0  Inclusion Criteria:\n\n1. Able to understand t...  
1  Inclusion Criteria:\n\n* Biopsy proven high-gr...  
2  Inclusion Criteria:\n\n* Reasonable exclusion ...  
3  Inclusion Criteria:\n\nInclusion criteria for ...